## Import libraries and dataset

In [1]:
import numpy as np
import pandas as pd

In [2]:
df = pd.read_csv('tweets.csv', index_col=False)
df.head()

Unnamed: 0    date                  id  \
0           0   Oct 7  784609194234306560   
1           1  Oct 10  785608815962099712   
2           2   Oct 8  784840992734064640   
3           3   Oct 8  784767399442653184   
4           4  Oct 10  785561269571026944   

                                         link  retweet  \
0  /realDonaldTrump/status/784609194234306560    False   
1  /realDonaldTrump/status/785608815962099712    False   
2  /realDonaldTrump/status/784840992734064641    False   
3  /realDonaldTrump/status/784767399442653184    False   
4  /realDonaldTrump/status/785561269571026946    False   

                                                text       author  
0    Here is my statement.pic.twitter.com/WAZiGoQqMQ  DonaldTrump  
1  Is this really America? Terrible!pic.twitter.c...  DonaldTrump  
2  The media and establishment want me out of the...  DonaldTrump  
3        Certainly has been an interesting 24 hours!  DonaldTrump  
4  Debate polls look great - thank you!\r\n#MAGA ...  DonaldTrump

In [3]:
df = df.drop(['Unnamed: 0'], axis=1)

In [4]:
df.head()

date                  id                                        link  \
0   Oct 7  784609194234306560  /realDonaldTrump/status/784609194234306560   
1  Oct 10  785608815962099712  /realDonaldTrump/status/785608815962099712   
2   Oct 8  784840992734064640  /realDonaldTrump/status/784840992734064641   
3   Oct 8  784767399442653184  /realDonaldTrump/status/784767399442653184   
4  Oct 10  785561269571026944  /realDonaldTrump/status/785561269571026946   

   retweet                                               text       author  
0    False    Here is my statement.pic.twitter.com/WAZiGoQqMQ  DonaldTrump  
1    False  Is this really America? Terrible!pic.twitter.c...  DonaldTrump  
2    False  The media and establishment want me out of the...  DonaldTrump  
3    False        Certainly has been an interesting 24 hours!  DonaldTrump  
4    False  Debate polls look great - thank you!\r\n#MAGA ...  DonaldTrump

## Data exploration

In [5]:
df.columns

Index(['date', 'id', 'link', 'retweet', 'text', 'author'], dtype='object')

In [6]:
df["date"][0]

'Oct 7'

In [7]:
type(df['retweet'][0])

numpy.bool_

In [8]:
df['author'].describe()

count           17216
unique              1
top       DonaldTrump
freq            17216
Name: author, dtype: object

In [9]:
from collections import Counter

In [10]:
authors = Counter(df['author'])

In [11]:
authors

Counter({'DonaldTrump': 17216})

In [12]:
retweets = Counter(df['retweet'])

In [13]:
retweets

Counter({False: 13579, True: 3637})

Since there are only Donald Trump tweets we don't need any column except for text.

## Tweets

In [14]:
tweets = df['text']

In [16]:
len(tweets)

17216

In [17]:
tweet0 = tweets[0]
tweet0

'Here is my statement.pic.twitter.com/WAZiGoQqMQ'

In [18]:
testtweets = tweets[:10]

In [19]:
for tweet in testtweets:
    print(tweet)

Here is my statement.pic.twitter.com/WAZiGoQqMQ
Is this really America? Terrible!pic.twitter.com/WiwC61PIFu
The media and establishment want me out of the race so badly -  I WILL NEVER DROP OUT OF THE RACE, WILL NEVER LET MY SUPPORTERS DOWN! #MAGA
Certainly has been an interesting 24 hours!
Debate polls look great - thank you!
#MAGA #AmericaFirstpic.twitter.com/4peQ3Sswdz
WHAT THEY ARE SAYING ABOUT THE CLINTON CAMPAIGN’S ANTI-CATHOLIC BIGOTRY: 
http://bit.ly/2dcbtvkCrooked 
Thank you! #MAGA #AmericaFirstpic.twitter.com/fG313wjlKm
I will be in Cincinnati, Ohio tomorrow night at 7:30pm- join me! #OhioVotesEarly #VoteTrumpPence16 
Tickets: https://www.donaldjtrump.com/schedule/register/cincinnati-oh2/ …pic.twitter.com/XUFuGc4Fg5
Very little pick-up by the dishonest media of incredible information provided by WikiLeaks. So dishonest! Rigged system!
Thank you Florida- a MOVEMENT that has never been seen before and will never be seen again. Lets get out & #VoteTrumpPence16 on 11/8! #MAGApic.

## Preprocessing

In [20]:
from gensim.utils import simple_preprocess, simple_tokenize
import re

In [21]:
query_string = tweet0
documents = tweets

stopwords = ['the', 'and', 'are', 'a']

def preprocess(doc):
    # Tokenize, clean up input document string
    doc = re.sub(r'pic.twitter.com\/+\w{0,}', 'picture_token', doc)
    #doc = sub(r'<img[^<>]+(>|$)', " image_token ", doc)
    #doc = sub(r'<[^<>]+(>|$)', " ", doc)
    #doc = sub(r'\[img_assist[^]]*?\]', " ", doc)
    doc = re.sub(r'http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+', " url_token ", doc)
    return [token for token in simple_preprocess(doc, min_len=0, max_len=float("inf")) if token not in stopwords]

# Preprocess the documents, including the query string
corpus = [preprocess(document) for document in documents]
query = preprocess(query_string)

In [22]:
query

['here', 'is', 'my', 'statement', 'picture_token']

In [23]:
for elem in corpus:
    print(elem)

['here', 'is', 'my', 'statement', 'picture_token']
['is', 'this', 'really', 'america', 'terrible', 'picture_token']
['media', 'establishment', 'want', 'me', 'out', 'of', 'race', 'so', 'badly', 'i', 'will', 'never', 'drop', 'out', 'of', 'race', 'will', 'never', 'let', 'my', 'supporters', 'down', 'maga']
['certainly', 'has', 'been', 'an', 'interesting', 'hours']
['debate', 'polls', 'look', 'great', 'thank', 'you', 'maga', 'americafirstpicture_token']
['what', 'they', 'saying', 'about', 'clinton', 'campaign', 's', 'anti', 'catholic', 'bigotry', 'url_token']
['thank', 'you', 'maga', 'americafirstpicture_token']
['i', 'will', 'be', 'in', 'cincinnati', 'ohio', 'tomorrow', 'night', 'at', 'pm', 'join', 'me', 'ohiovotesearly', 'votetrumppence', 'tickets', 'url_token', 'picture_token']
['very', 'little', 'pick', 'up', 'by', 'dishonest', 'media', 'of', 'incredible', 'information', 'provided', 'by', 'wikileaks', 'so', 'dishonest', 'rigged', 'system']
['thank', 'you', 'florida', 'movement', 'that',

['there', 'is', 'url_token']
['scott__marx', 'can', 't', 'wait', 'to', 'hear', 'realdonaldtrump', 'run', 'for', 'president', 'fix', 'our', 'country', 'trump']
['thanks', 'i', 'won', 't', 'let', 'you', 'down', 'url_token']
['great', 'thanks', 'url_token']
['realterrypatton', 'realdonaldtrump', 'jencromartie', 'do', 'it', 'mr', 'trump', 'we', 'screwed', 'if', 'you', 'don', 't', 'i', 'agree']
['dillonconrad', 'if', 'realdonaldtrump', 'ran', 'for', 'president', 'in', 'i', 'd', 'be', 'one', 'happy', 'camper']
['ipatriotmedia', 'texans', 'do', 'not', 'support', 'rinos', 'we', 'damn', 'sure', 'don', 't', 'support', 'jebbush', 'texans', 'want', 'leadership', 'we', 'want', 'realdonaldtrump']
['marcopolomacon', 'realdonaldtrump', 'what', 'you', 'waiting', 'for', 'we', 'waiting', 'for', 'you', 'to', 'make', 'america', 'great', 'again', 'please', 'run', 'june', 'th']
['jencromartie', 'realdonaldtrump', 'needs', 'to', 'run', 'for', 'president', 'election', 'donaldtrump']
['entrepreneurs', 'review',

['olyagradova', 'realdonaldtrump', 'please', 'tell', 'me', 'you', 'at', 'least', 'considering', 'running', 'for', 'president', 'please', 'please', 'please', 'i', 'am']
['pianobecca', 'donald', 'we', 'realy', 'need', 'you', 'for', 'you', 'handsome', 'but', 'mostly', 'you', 're', 'intelligent', 'we', 'need', 'you', 'too', 'make', 'america', 'great', 'again']
['smchenrypower', 'carter', 'was', 'very', 'unsuccessful', 'but', 'aging', 'has', 'him', 'wiser', 'quite', 'strong', 'in', 'foreign', 'relations', 'but', 'obama', 'is', 'hopeless', 'worst']
['wesley_minga', 'realdonaldtrump', 'you', 're', 'genius', 'thank', 'you', 'you', 'so', 'correct']
['jerrysan', 'now', 'that', 'is', 'combo', 'he', 'needs', 'ride', 'along', 'rt', 'jebburtonracing', 'got', 'to', 'meet', 'man', 'donald', 'trump', 'picture_token']
['tylerthekicker', 'donald', 'trump', 'by', 'mac', 'miller', 'will', 'forever', 'be', 'great', 'song', 'many', 'agree']
['southheastt', 'on', 'this', 'joyous', 'holiday', 'i', 'am', 'thank

['also', 'great', 'comeback', 'by', 'new', 'york', 'jets', 'that', 'game', 'was', 'over', 'until', 'really', 'dumb', 'defensive', 'play', 'by', 'tampa', 'amazing']
['tony', 'romo', 'just', 'made', 'great', 'play', 'giants', 'getting', 'killed']
['great', 'comeback', 'by', 'tom', 'brady', 'new', 'england']
['new', 'york', 'giants', 'looking', 'really', 'bad', 'so', 'far', 'tonight', 'does', 'not', 'get', 'much', 'worse', 'than', 'this']
['toughnewworld', 'i', 'may', 'not', 'always', 'agree', 'with', 'realdonaldtrump', 'statements', 'but', 'he', 'does', 'have', 'good', 'looking', 'line', 'of', 'shirts', 'ties']
['doing', 'commercial', 'for', 'nflonfox', 'lots', 'of', 'fun', 'url_token']
['seanofkbio', 'trumpgolflinks', 'realdonaldtrump', 'what', 'coarse', 'what', 'service', 'jewel', 'of', 'scotland', 'picture_token']
['gretawire', 'presobama', 'is', 'not', 'busy', 'talking', 'to', 'congress', 'about', 'syria', 'he', 'is', 'playing', 'golf', 'go', 'figure']
['ashley_rad', 'realdonaldtrump

['social', 'media', 'has', 'changed', 'news', 'communication', 'landscape', 'for', 'good', 'everything', 'must', 'be', 'up', 'to', 'date', 'by', 'second', 'instead', 'of', 'hour', 'or', 'day']
['former', 'classmate', 'roy', 'eaton', 'has', 'published', 'great', 'book', 'makers', 'shakers', 'takers', 'check', 'it', 'out', 'url_token']
['obama', 's', 'own', 'top', 'donor', 'is', 'now', 'laying', 'employees', 'off', 'lowering', 'hours', 'in', 'anticipation', 'of', 'obama', 'care', 'url_token', 'new', 'reality']
['i', 'never', 'did', 'give', 'anybody', 'hell', 'i', 'just', 'told', 'truth', 'they', 'thought', 'it', 'was', 'hell', 'harry', 's', 'truman']
['to', 'aspiring', 'entrepreneurs', 'always', 'remember', 'that', 'if', 'your', 'enemies', 'aren', 't', 'talking', 'about', 'you', 'then', 'you', 'aren', 't', 'doing', 'well', 'must', 'work', 'harder']
['gen', 'petraeus', 'has', 'agreed', 'to', 'testify', 'in', 'senate', 'on', 'benghazi', 'i', 'will', 'be', 'watching']
['you', 'can', 'have',

['habitual', 'vacationer', 'barackobama', 'is', 'now', 'in', 'hawaii', 'this', 'vacation', 'is', 'costing', 'taxpayers', 'milion', 'while', 'there', 'is', 'unemployment']
['in', 'order', 'to', 'preserve', 'my', 'options', 'guarantee', 'that', 'barackobama', 'is', 'defeated', 'i', 'changed', 'my', 'voter', 'registration', 'to', 'independent']
['keystone', 'pipeline', 'will', 'create', 'jobs', 'make', 'us', 'less', 'energy', 'dependent', 'from', 'middle', 'east', 'barackobama', 'says', 'no']
['safest', 'way', 'to', 'preserve', 'medicare', 'is', 'with', 'robust', 'vibrant', 'economy', 'we', 'should', 'lower', 'corporate', 'capital', 'gain', 'taxes', 'immediately']
['week', 'after', 'biden', 'says', 'that', 'taliban', 'is', 'not', 'our', 'enemy', 'taliban', 'demand', 'that', 'we', 'pay', 'iraq', 'for', 'year', 'occupation', 'url_token']
['even', 'if', 'barackobama', 'stays', 'in', 'dc', 'taxpayers', 'will', 'pay', 'millions', 'for', 'his', 'hawaii', 'vacation', 'when', 'americans', 'strugg

## Model loading and prediction

In [24]:
import gensim.downloader as api
from gensim.corpora import Dictionary
from gensim.models import TfidfModel
from gensim.models import WordEmbeddingSimilarityIndex
from gensim.similarities import SparseTermSimilarityMatrix
from gensim.similarities import SoftCosineSimilarity

In [25]:
# Load the model: this is a big file, can take a while to download and open
glove = api.load("glove-wiki-gigaword-50")    
similarity_index = WordEmbeddingSimilarityIndex(glove)

# Build the term dictionary, TF-idf model
dictionary = Dictionary(corpus+[query])
tfidf = TfidfModel(dictionary=dictionary)

# Create the term similarity matrix.  
similarity_matrix = SparseTermSimilarityMatrix(similarity_index, dictionary, tfidf)

In [26]:
# Compute Soft Cosine Measure between the query and the documents.
# From: https://github.com/RaRe-Technologies/gensim/blob/develop/docs/notebooks/soft_cosine_tutorial.ipynb
query_tf = tfidf[dictionary.doc2bow(query)]

index = SoftCosineSimilarity(
            tfidf[[dictionary.doc2bow(document) for document in corpus]],
            similarity_matrix)

doc_similarity_scores = index[query_tf]

# Output the sorted similarity scores and documents
sorted_indexes = np.argsort(doc_similarity_scores)[::-1]
for idx in sorted_indexes:
    print(f'{idx} \t {doc_similarity_scores[idx]:0.3f} \t {documents[idx]}')

C:\Users\Gremy Trullier\anaconda3\lib\site-packages\gensim\similarities\termsim.py:358: RuntimeWarning: divide by zero encountered in true_divide
  Y = np.multiply(Y, 1 / np.sqrt(Y_norm))
C:\Users\Gremy Trullier\anaconda3\lib\site-packages\gensim\similarities\termsim.py:358: RuntimeWarning: invalid value encountered in multiply
  Y = np.multiply(Y, 1 / np.sqrt(Y_norm))


0 	 1.000 	 Here is my statement.pic.twitter.com/WAZiGoQqMQ
3064 	 0.916 	 "@MDTaylorJr Everyone else have fun being politically correct. Meanwhile, @realDonaldTrump is speaking the truth. #Trump2016"
3405 	 0.895 	 My recent statement re: @macys -- We must have strong borders & stop illegal immigration now!… https://instagram.com/p/4mS9POGhVe/ 
11658 	 0.892 	 Just arrived at Trump National Doral, saying hello to all the great players. This place is amazing.Come Thursday & see for yourselves!
7088 	 0.888 	 It’s Thursday. Which brand of eyeliner is the nation’s worst AG @AGSchneiderman wearing today?
4840 	 0.878 	 "@Doris22: RT  The CPAC Team is excited to announce that @realDonaldTrump will be speaking at CPAC 2015! #CPAC2015 pic.twitter.com/D9YoUWoQ6M"
13256 	 0.876 	 It's Thursday. How much money did Barack Obama waste today on crony green energy projects?
14884 	 0.876 	 It’s Thursday.  How much did OPEC steal from all of us today?
8377 	 0.876 	 It’s Thursday. How many people ha

2280 	 0.486 	 "@jaxsiete: @realDonaldTrump Love your sense of humor...LOL Your rallies are amazing. We're standing behind you 1000%:)" @FoxNews
961 	 0.486 	 Lyin' Ted Cruz is now trying to convince prople that his problems with The National Enq.were caused by me. I had NOTHING to do with story!
318 	 0.485 	 Crooked Hillary said that I "couldn't handle the rough and tumble of a political campaign." Really,I just beat 16 people and am beating her!
11438 	 0.485 	 “Here’s something about Donald Trump, he’s got a top rated show on TV and everything he says becomes a headline.”-@DLoesch  All true!
2740 	 0.485 	 "@Hashtag1USA: @realDonaldTrump Trump rocked Iowa today heard his message was positive and built much enthusiasm among the voters #Trump2016
2860 	 0.485 	 Jeb Bush just talked about my border proposal to build a "fence." It's not a fence, Jeb, it's a WALL, and there's a BIG difference!
11519 	 0.485 	 .@dallasmavs is 1-12 against the Western Conference’s top four seeds after Sun

9119 	 0.393 	 The big golf course project on the water by the Whitestone Bridge in NYC that has been under construction for many years now complete-GREAT!
155 	 0.393 	 The polls are close so Crooked Hillary is getting out of bed and will campaign tomorrow.Why did she hammer 13 devices and acid-wash e-mails?
4477 	 0.393 	 Entrepreneurs: When negotiating, don't be an open book. Know that the only person on your side might be yourself.
4953 	 0.393 	 "@ApprenticeNBC: By the way — you will NOT want to miss #Phonegate next week on #CelebApprentice. That's all we're gonna say."
10302 	 0.393 	 James Gandolfini was a remarkable talent.  He was also a decent man.  We will all miss him.
6917 	 0.393 	 .@McIlroyRory  Great job Rory - you have the heart and talent of a great champion. Work hard and win many more! See you at Turnberry.
774 	 0.393 	 Can you believe Crooked Hillary said, "We are going to put a whole lot of coal miners&coal companies out of business." She then apologized.
1197 	 

17027 	 0.335 	 If Obama has to re-fight this fight next year he loses  -- "Watch the fine details in every deal" -- The Art of the Deal
14006 	 0.335 	 Great players in sports make the game fun to watch. @DerekJeter has continued to impress with another amazing season. Absolute professional.
16066 	 0.335 	 Great players in sports make the game fun to watch. @DerekJeter has continued to impress with another amazing season. Absolute professional.
16910 	 0.335 	 Why is the UN condemning @Israel and doing nothing about Syria? What a disgrace.
9021 	 0.335 	 Obama can open the Mall for illegals to protest our country yet he continues to barricade WWII memorial. That’s an absolute disgrace.
10615 	 0.335 	 "@Gurning_Chimp: @realDonaldTrump @bluejoni No, YOU hate wind power as YOU think it'll mess with YOUR golf course." That's true also!
1705 	 0.335 	 "@drdoucette: #MissUniverse DonaldTrump must be overjoyed that as soon as he sells the pageant it goes off the rails. We need you Mr Trump

15153 	 0.249 	 The polls & momentum  are trending towards @MittRomney. Don't let the hurricane change your thinking!
7356 	 0.249 	 Negotiation tip: Know exactly what you want and focus on that. Trust your instincts, even after you've honed your skills.
7547 	 0.249 	 Young entrepreneurs –  Remember that your first deals are the most important of your career. Win & gain confidence.
7284 	 0.249 	 "@phagan2: @realDonaldTrump your children are smart and capable. You must take the reins and get the USA back #1"  It can be done.
4300 	 0.249 	 "@KnucklDraginSam: @realDonaldTrump @Chris_Owens1213 @HillaryClinton Yeah, first question, list your major accomplishments.  #Trump4Prez"
7394 	 0.249 	 "@tquoteseday: If you're interested in 'balancing' work and pleasure, stop! Instead make your work more pleasurable. - Donald Trump"
11509 	 0.249 	 "@Ashbash032: @realDonaldTrump don't waste time on your haters!Let them hate, you keep building your empire #respect #jealoushaters"  Great!
2425 	 0.2

9720 	 0.147 	 “Definiteness of purpose is the starting point of all achievement.” - W. Clement Stone
9718 	 0.147 	 "Patience is the greatest of all virtues." -- Cato
2620 	 0.147 	 Rubio is totally owned by the lobbyists and special interests. A lightweight senator with the worst voting record in Senate. Lazy!
906 	 0.147 	 It is so great to be back home! Looking forward to a great rally tonight in Bethpage, Long Island!
16841 	 0.147 	 The death tax should be abolished -- the Government is  simply taxing you twice. It is also a job killer.
16842 	 0.147 	 Solyndra's government loan and subsequent bankruptcy  prove that @BarackObama is both corrupt and inept.
9018 	 0.147 	 Obama is the most profligate deficit & debt spender in our nation’s history. Doubled debt (cont) http://tl.gd/n_1rpk61e 
9695 	 0.147 	 FACT – the reason why Americans have to worry about a government shutdown is because Obama refuses to pass a budget.
9693 	 0.147 	 If the gov't shuts down, it is because Obama wa

17186 	 0.000 	 "A lot of people have imagination, but can't execute--you have to execute with the imagination." --Donald J. Trump http://tinyurl.com/pqpfvm
1328 	 0.000 	 MAKE AMERICA GREAT AGAIN!
16952 	 0.000 	 The Solyndra Scandal--@BarackObama's $500Million photo op. He loves wasting our money.
16723 	 0.000 	 What a shock! The U.S. Capitol Christmas tree pays homage @BarackObama but failed to mention Jesus.
17188 	 0.000 	 - More hysterical DSRL videos featuring Donald Trump and "Double Trump" plus enter Golden Lick Race Sweepstakes: http://tinyurl.com/6asujj
16725 	 0.000 	 "People who have the ability to work should. But with the government happy to send checks, too many of them don't." #TimeToGetTough
16949 	 0.000 	 "It  doesn't cost any money to think bigger."  -- The Art of the Deal
1318 	 0.000 	 THANK YOU- Clemson, South Carolina! #MakeAmericaGreatAgain #SCPrimarypic.twitter.com/FgACmaFxxc
1315 	 0.000 	 Remember, it was the Republican Party, with the help of Conservative

In [27]:
query, len(query_tf)

(['here', 'is', 'my', 'statement', 'picture_token'], 5)

In [28]:
for i,idx in enumerate(sorted_indexes):
    if i > 10:
        break
    print(idx, f'{doc_similarity_scores[idx]:0.3f}', documents[idx])

0 1.000 Here is my statement.pic.twitter.com/WAZiGoQqMQ
3064 0.916 "@MDTaylorJr Everyone else have fun being politically correct. Meanwhile, @realDonaldTrump is speaking the truth. #Trump2016"
3405 0.895 My recent statement re: @macys -- We must have strong borders & stop illegal immigration now!… https://instagram.com/p/4mS9POGhVe/ 
11658 0.892 Just arrived at Trump National Doral, saying hello to all the great players. This place is amazing.Come Thursday & see for yourselves!
7088 0.888 It’s Thursday. Which brand of eyeliner is the nation’s worst AG @AGSchneiderman wearing today?
4840 0.878 "@Doris22: RT  The CPAC Team is excited to announce that @realDonaldTrump will be speaking at CPAC 2015! #CPAC2015 pic.twitter.com/D9YoUWoQ6M"
13256 0.876 It's Thursday. How much money did Barack Obama waste today on crony green energy projects?
14884 0.876 It’s Thursday.  How much did OPEC steal from all of us today?
8377 0.876 It’s Thursday. How many people have lost their healthcare today?
1282

In [29]:
for elem in documents:
    print(elem)

Here is my statement.pic.twitter.com/WAZiGoQqMQ
Is this really America? Terrible!pic.twitter.com/WiwC61PIFu
The media and establishment want me out of the race so badly -  I WILL NEVER DROP OUT OF THE RACE, WILL NEVER LET MY SUPPORTERS DOWN! #MAGA
Certainly has been an interesting 24 hours!
Debate polls look great - thank you!
#MAGA #AmericaFirstpic.twitter.com/4peQ3Sswdz
WHAT THEY ARE SAYING ABOUT THE CLINTON CAMPAIGN’S ANTI-CATHOLIC BIGOTRY: 
http://bit.ly/2dcbtvkCrooked 
Thank you! #MAGA #AmericaFirstpic.twitter.com/fG313wjlKm
I will be in Cincinnati, Ohio tomorrow night at 7:30pm- join me! #OhioVotesEarly #VoteTrumpPence16 
Tickets: https://www.donaldjtrump.com/schedule/register/cincinnati-oh2/ …pic.twitter.com/XUFuGc4Fg5
Very little pick-up by the dishonest media of incredible information provided by WikiLeaks. So dishonest! Rigged system!
Thank you Florida- a MOVEMENT that has never been seen before and will never be seen again. Lets get out & #VoteTrumpPence16 on 11/8! #MAGApic.

Made a speech in Arkansas last night before a record GOP crowd. Great spirit and amazing people. MAKE AMERICA GREAT AGAIN!
It's driving @ariannahuff & the money losing @HuffingtonPost post crazy that I am #1 in their poll and they only write bad stories about me!
The liberal clown  @ariannahuff told her minions at the money losing @HuffingtonPost to cover me as enterainment. I am #1 in Huff Post Poll.
Response to Huffington Post- http://on.fb.me/1OkZm82 
“God's word is the same, yesterday and today and a million years from now.” - @Franklin_Graham
We will no longer be silent. We can take our country back! Let’s Make America Great Again! https://www.donaldjtrump.com/ 
MILITARY LIVES MATTER! END GUN FREE ZONES! OUR SOLDIERS MUST BE ABLE TO PROTECT THEMSELVES! THIS HAS TO STOP!
I had thousands join me in New Hampshire last night! @HillaryClinton had 68. The #SilentMajority is fed up with what is going on in America!
"@Tamaralynn212: @RWSurferGirl  @realDonaldTrump The whole Gov. needs to 

"@DNorrell: @Judgenap @freedomlives999 DonaldTrump trump is the only non politician who will actually do what he says. All the rest all talk
"@davevin73: @realDonaldTrump You should be president, I signed up for Twitter just to tell you this. A lot of Americans feel the same way"
"@2014_vince: I am praying sir u wil b president in 2016..end the scam of foreign aid..make other countries PAY for help..you INSPIRE..."
"@TrumpFerryPoint: Two great families come together to create a masterpiece. #GrandOpening DonaldTrump @jacknicklaus pic.twitter.com/R1AVPqho5a"
"@therealtommydel:1 & only POTUS candidate 2 support Tom Brady deserves the White House. Clear judgment & common sense for USA ! #FreeBrady"
.@AnnCoulter's new book-- "Adios, America! The Left's Plan to Turn Our Country into a Third World Hellhole"-- is a great read. Good job!
“Everyone's dream can come true if you just stick to it and work hard.” - @serenawilliams
Entrepreneurs: Realize that persistence can go a long way. Being stu

"@BarbaraSMayer: @realDonaldTrump You are right about the Ebola patients. It's a deadly virus, and they shouldn't bring them to the US."
If you read my last number of tweets, only one opinion can be formed - that our President, and therefore "leader," is grossly incompetent!
The ObamaCare website is in the news again - it is turning out to cost even more than previously thought, AND IT DOESN'T WORK! Big trouble!
So many lives and two trillion dollars wasted, and our worst enemies will get the 2nd largest oil reserves in the World. Such stupid leaders
Just as I have been predicting for years, Iraq will fall to the people that hate  the U.S. the most - just outside of Baghdad."Keep the oil"
The U.S. cannot allow EBOLA infected people back. People that go to far away places to help out are great-but must suffer the consequences!
.@David_Cameron  Why do you give Scotland so much money to destroy their magnificent land with wind turbines-causing massive taxes & E bills
.@David_Cameron As Pr

"@Matthew_Erdman: DonaldTrump You built a beautiful high-rise, you pay your taxes, you should be able to put up whatever signage you want."
The Iraqi Army is useless. President Obama, stay the hell out of Iraq (we should never have been there in the first place).
"@russell_triston: @realDonaldTrump Would make a great Commander in Chief. True intelligence. Common sense, economy knowledge, leadership."
We should never have gone into Iraq but, once in, should have gotten out a lot faster. MAKE AMERICA GREAT AGAIN!
"@nikkio: I know I'm a day early for your weekend celebrations-Happy Birthday Donald! Looking forward to your surprises for 2014-2015 Thanks
"@bestgolfleague: I don't understand the all the fuss. The building is an exquisite edition to our skyline. pic.twitter.com/WvafTAhfWF"
Before I bought the site, the Sun Times had the biggest, ugliest sign Chicago has ever seen. Mine is magnificent and popular.
In answer to your questions about my favorite impersonator, the answer is Darrel

Army officer who led a sexual abuse prevention unit was just fired after being charged with violently going after his wife.What is going on?
America's top Army general has warned of a crisis unless sexual abuse in the military is quickly brought undet control.Forces greatly hurt!
"@IcyJordan: @realDonaldTrump do you like LeBron as a player and person? @KingJames"  LeBron is a great player and a great guy!
"@jakeklopp24: @realDonaldTrump what's it like to be Donald Trump?"  Believe it or not, it ain't easy!
"@ahatwearer: @realDonaldTrump why are you suing an old lady?"  Because she is rich and owes me money - I am not stupid!
"@MikeMessina_: @realDonaldTrump needs to run for President! He would be the best leader!"  Thanks Mike.
"@ricksmi54256322: @realDonaldTrump i can't wait til ur president the world will be a better place" If I ran and won, so true (& thanks)!
Looks like we will have a pervert running for mayor after all - just what New York City needs - and he will revert back to f

Jodi should try but the Govt. should not make a deal - no jury could be dumb enough to let her off (but you never know, look at OJ & others)
Jodi Arias has stated that she follows me on twitter so I really hate to be saying that she is guilty but sadly, she is as guilty as it gets
"@anthonyeding: No doubt the @realDonaldTrump would have been a better president than Obama"   TRUE!
@hdiallo   Why do you follow me creepy stalker?
"@zack_21: @realDonaldTrump @hdiallo @dblsolo7 class act there donald. How dare u call this beautiful women these names. You said beautiful?
"@teaparty321: @realDonaldTrump if you run for president in 2016, I hope you talk about your success instead of hiding it." No doubt!
"@hdiallo: @dblsolo7 @realDonaldTrump That hair is a hot mess & shows he gas no class or style!"   Yea, you're a real beauty!
Just took a look at Time Magazine-looks really flimsy like a free handout at a parking lot! The sad end is coming-just like Newsweek!
“Don’t let the fear of striking ou

An 'extremely credible source' has called my office & told me that @BarackObama applied to Occidental as a foreign student--think about it!
China's Olympic training program is abusive http://bit.ly/OFJ22I  It is modern day slavery & shameful. Their (cont) http://tl.gd/in6clo 
Our athletes in the Olympics are proving once again to be the greatest competitors in the world. Makes us proud to be Americans.
Congratulations to @MichaelPhelps on concluding the greatest Olympic career ever. You have made us all very proud.
Congratulations to Gabby Douglas on winning the Gold for the USA in gymnastics. She is terrific!
Over 150,000 more of our fellow Americans dropped out of the workforce in July. @BarackObama is a disaster!
New job numbers once again show no growth or recovery. Unemployment has been over 8% for 41 straight months--now up to 8.3%
Good--@marcorubio is trying to eliminate the tax on Olympic medals http://bit.ly/QfnWLt   Our athletes should not be taxed on their wins.
"Capital isn

"The @BarackObama administration is far more enthusiastic about boosting food-stamp enrollment than about preventing fraud." #TimeToGetTough
What will be @RickSantorum's excuse tomorrow after @MittRomney wins Wisconsin and Maryland? Time for Rick to face reality and drop out.
The US should not give a penny of foreign aid to Egypt if the Muslim Brotherhood takes over the country. We (cont) http://tl.gd/gp6410 
America's competitors love @BarackObama. @MedvedevRussiaE says @BarackObama has been "the best 3 years" for Russiahttp://bit.ly/H8RUyT 
Waste! With a $16T debt and $1T budget deficit, @BarackObama is sending $770M overseas "to fight global warming"http://bit.ly/GSEWRr 
"The worst thing you can possibly do in a deal is seem desperate to make it." #TheArtofTheDeal
"I like thinking big. I always have. To me it's very simple: if you're going to be thinking anyway, you might as (cont) http://tl.gd/gnhon6 
A study says @Autism is out of control--a 78% increase in 10 years. Stop giving m